## At this point, I already have the data in geojson format and want to:
#### 1. merge multiple geojson of the same format into a single geojson
#### 2. add properties based on many to one relationships between a property already in the geojson and a csv sheet with three columns

In [1]:
#### Imports for parts #1 & #2
from bs4 import BeautifulSoup # For HTML parsing
from urllib.request import urlopen
import re # Regular expressions
from time import sleep # To prevent overwhelming the server between connections
from collections import Counter # Keep track of our term counts
from nltk.corpus import stopwords # Filter out stopwords, such as 'the', 'or', 'and'
import pandas as pd # For converting results to a dataframe and bar chart plots
%matplotlib inline
import json
import csv

##### Import modules for google API and geoJSON parts. Only duplicate is json
import requests
import configparser
import json
import geojson
from geojson import Point, Feature, FeatureCollection
# https://github.com/frewsxcv/python-geojson
import time
import pandas as pd

In [2]:
feat_collec_intake_1of3 = pd.read_json('../DATA/test_geojson_Everything_1of3_v2.geojson')
feat_collec_intake_1of3

features               type
0     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
3     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
4     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
6     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
7     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
8     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
9     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
10    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
11    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
12    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
13    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
14    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
15    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
16    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
17    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
18    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
19    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
20    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
21    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
22    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
23    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
24    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
25    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
26    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
27    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
28    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
29    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
...                                                 ...                ...
2860  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2861  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2862  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2863  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2864  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2865  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2866  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2867  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2868  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2869  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2870  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2871  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2872  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2873  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2874  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2875  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2876  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2877  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2878  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2879  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2880  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2881  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollecti

In [3]:
## test writing from pd to json
test_json = feat_collec_intake_1of3.to_json("../DATA/test_json.json")

In [4]:
feat_collec_intake_2of3 = pd.read_json('../DATA/test_geojson_Everything_2of3_v2.geojson')
feat_collec_intake_2of3

features               type
0     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
3     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
4     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
6     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
7     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
8     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
9     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
10    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
11    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
12    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
13    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
14    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
15    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
16    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
17    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
18    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
19    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
20    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
21    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
22    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
23    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
24    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
25    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
26    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
27    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
28    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
29    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
...                                                 ...                ...
1278  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1279  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1280  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1281  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1282  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1283  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1284  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1285  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1286  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1287  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1288  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1289  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1290  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1291  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1292  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1293  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1294  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1295  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1296  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1297  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1298  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1299  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollecti

In [5]:
feat_collec_intake_3of3 = pd.read_json('../DATA/test_geojson_Everything_3of3_v2.geojson')
feat_collec_intake_3of3

features               type
0     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
3     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
4     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
6     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
7     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
8     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
9     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
10    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
11    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
12    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
13    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
14    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
15    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
16    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
17    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
18    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
19    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
20    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
21    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
22    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
23    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
24    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
25    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
26    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
27    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
28    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
29    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
...                                                 ...                ...
1524  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1525  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1526  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1527  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1528  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1529  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1530  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1531  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1532  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1533  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1534  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1535  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1536  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1537  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1538  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1539  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1540  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1541  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1542  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1543  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1544  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1545  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollecti

In [6]:
merged_feat_collec_pd_123of3vB = pd.concat([feat_collec_intake_1of3, feat_collec_intake_2of3, feat_collec_intake_3of3], ignore_index=True)

In [7]:
merged_feat_collec_pd_123of3vB

features               type
0     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
1     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
2     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
3     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
4     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
6     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
7     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
8     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
9     {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
10    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
11    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
12    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
13    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
14    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
15    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
16    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
17    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
18    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
19    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
20    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
21    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
22    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
23    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
24    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
25    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
26    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
27    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
28    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
29    {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
...                                                 ...                ...
5722  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5723  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5724  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5725  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5726  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5727  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5728  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5729  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5730  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5731  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5732  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5733  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5734  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5735  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5736  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5737  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5738  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5739  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5740  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5741  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5742  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollection
5743  {'geometry': {'type': 'Point', 'coordinates': ...  FeatureCollecti

In [8]:
merged_feat_collec_pd_123of3vB['features'][0]

{'geometry': {'coordinates': [-95.3996299, 29.70984659999999],
  'type': 'Point'},
 'properties': {'address': '6565 Fannin St, Houston, TX 77030, United States',
  'commpany_searched_for': 'Houston+Methodist+Houston+Texas',
  'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55',
  'job_title': 'Biochemistry',
  'name': 'Methodist Hospital Emergency Services',
  'photos': [],
  'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA',
  'rating': 3.4,
  'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv',
  'types': ['hospital', 'point_of_interest', 'establishment']},
 'type': 'Feature'}

In [9]:
merged_feat_collec_pd_123of3vB['features'][0]['geometry']

{'coordinates': [-95.3996299, 29.70984659999999], 'type': 'Point'}

In [10]:
junk_afsdfasdf = merged_feat_collec_pd_123of3vB['features'][0]['properties']
junk_afsdfasdf

{'address': '6565 Fannin St, Houston, TX 77030, United States',
 'commpany_searched_for': 'Houston+Methodist+Houston+Texas',
 'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55',
 'job_title': 'Biochemistry',
 'name': 'Methodist Hospital Emergency Services',
 'photos': [],
 'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA',
 'rating': 3.4,
 'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv',
 'types': ['hospital', 'point_of_interest', 'establishment']}

In [11]:
junk_afsdfasdf['nonsense']="no really nonsense"
junk_afsdfasdf

{'address': '6565 Fannin St, Houston, TX 77030, United States',
 'commpany_searched_for': 'Houston+Methodist+Houston+Texas',
 'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55',
 'job_title': 'Biochemistry',
 'name': 'Methodist Hospital Emergency Services',
 'nonsense': 'no really nonsense',
 'photos': [],
 'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA',
 'rating': 3.4,
 'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv',
 'types': ['hospital', 'point_of_interest', 'establishment']}

In [12]:
merged_feat_collec_pd_123of3vB['features'][0]['properties']

{'address': '6565 Fannin St, Houston, TX 77030, United States',
 'commpany_searched_for': 'Houston+Methodist+Houston+Texas',
 'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55',
 'job_title': 'Biochemistry',
 'name': 'Methodist Hospital Emergency Services',
 'nonsense': 'no really nonsense',
 'photos': [],
 'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA',
 'rating': 3.4,
 'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv',
 'types': ['hospital', 'point_of_interest', 'establishment']}

In [13]:
target_cols = ['MedDescription', 'Min', 'Max', 'Days Unused']


NameError: name 'df1' is not defined

### Load in job title csv as pandas df

In [16]:
job_names = pd.read_csv('../DATA/science_jobs_v2.csv')
job_names

Job_Title likely_Industry field_of_science
0              Bioanalytical Scientist          health          biology
1                           Biochemist          health          biology
2                         Biochemistry          health          biology
3    Bioinformatics Research Scientist          health          biology
4                  Biological Engineer          health          biology
5                            Biologist          health          biology
6                            biology            health          biology
7                        biomechanical          health          biology
8                 Biomedical scientist          health          biology
9                           biophysics          health          biology
10                           Cell Line          health          biology
11                       Clinical Data          health          biology
12              Clinical Data Research          health          biology
13     Clinical Pharmacology Professor          health          biology
14         Clinical Pharmacy Assistant          health          biology
15         Clinical Research Associate          health          biology
16                      Drug Evaluator          health        chemistry
17     Drug Regulatory Affairs Manager          health        chemistry
18      Environmental Health Scientist          health          biology
19                   Genetic Counselor          health          biology
20                     Health Research          health          biology
21                   Health Technology          health          biology
22                  Healthcare science          health          biology
23         Hospital Research Assistant          health          biology
24                Immunology Scientist          health          biology
25                        Life Science          health          biology
26                             Medical          health          biology
27                      Medical Center          health          biology
28                  medical Laboratory          health          biology
29        Medical laboratory scientist          health          biology
..                                 ...             ...              ...
135                  reservoir modeler       petroleum    earth science
136                    rock Laboratory       petroleum    earth science
137                    sedimentologist       petroleum    earth science
138                       stratigraphy       petroleum    earth science
139                    subsea engineer       petroleum      engineering
140                        aeronautics           space      engineering
141                          Aerospace           space      engineering
142                       astrobiology           space          biology
143                     Astrochemistry           space        chemistry
144                     astromaterials           space    earth science
145                          Astronaut           space          physics
146                         Astronomer           space          physics
147                          astronomy           space          physics
148                       astrophysics           space          physics
149                     Food chemistry           space        chemistry
150                       heliophysics           space          physics
151        International Space Station           space          generic
152               Johnson Space Center           space          generic
153                              lunar           space    earth science
154                 materials engineer           space      engineering
155                               NASA           space          generic
156                          Physicist           space          physics
157                            physics           space          physics
158                        Planetary             space    earth scien

In [17]:
job_names["Job_Title"]

0                Bioanalytical Scientist
1                             Biochemist
2                           Biochemistry
3      Bioinformatics Research Scientist
4                    Biological Engineer
5                              Biologist
6                              biology  
7                          biomechanical
8                   Biomedical scientist
9                             biophysics
10                             Cell Line
11                         Clinical Data
12                Clinical Data Research
13       Clinical Pharmacology Professor
14           Clinical Pharmacy Assistant
15           Clinical Research Associate
16                        Drug Evaluator
17       Drug Regulatory Affairs Manager
18        Environmental Health Scientist
19                     Genetic Counselor
20                       Health Research
21                     Health Technology
22                    Healthcare science
23           Hospital Research Assistant
24              

In [18]:
job_names["likely_Industry"][1]

'health'

In [80]:
def addSciAndIndToFeature(featureCollectionInput,jobSciIndustryInput):
    #featureCollectionInput 
    #print("featureCollectionInput['features']",featureCollectionInput['features'])
    for item in enumerate(featureCollectionInput['features']):
        row = item[1]
        # row = featureCollectionInput['features'][each]
        #row = each
        #print("1 row",row)
        #print("2 row['properties']",row['properties'])
        #print("3 row['properties']['job_title']",row['properties']['job_title'])
        #print("4 jobSciIndustryInput",jobSciIndustryInput)
        number = -1
        for each2 in jobSciIndustryInput:
            number += 1
            print("number = ",number)
            ##print("5 each2",each2)
            ##print("6 each2[0]",each2[0])
            print("7 each2['likely_Industry']",jobSciIndustryInput["likely_Industry"][number])
            if row['properties']['job_title'] == jobSciIndustryInput["likely_Industry"][number]:
                row['properties']['industry'] = jobSciIndustryInput["likely_Industry"][number]
                # need assign new row back to dataframe
                featureCollectionInput.ix[item[0,0]
                print("row['properties']['industry']",row['properties']['industry'])
    return featureCollectionInput

In [133]:
for i in enumerate(merged_feat_collec_pd_123of3_edit_vC['features']):
    print(i)
                                                         

(0, {'geometry': {'type': 'Point', 'coordinates': [-95.3996299, 29.70984659999999]}, 'properties': {'job_title': 'Biochemistry', 'name': 'Methodist Hospital Emergency Services', 'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv', 'commpany_searched_for': 'Houston+Methodist+Houston+Texas', 'photos': [], 'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA', 'types': ['hospital', 'point_of_interest', 'establishment'], 'rating': 3.4, 'address': '6565 Fannin St, Houston, TX 77030, United States', 'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55', 'nonsense': 'no really nonsense'}, 'type': 'Feature'})
(1, {'geometry': {'type': 'Point', 'coordinates': [-95.41891590000002, 29.7329608]}, 'properties': {'job_title': 'Biochemistry', 'name': 'The Princeton Review', 'reference': 'CmRRAAAAB5JBqvaGgOpt90_tQYMjE-ceP5L-AocDG1cABUmsOphY4fyk9d7BWVsObRIlUrHE94KBb4H5HKlQsbbvcD8CzzgbgjQ0r

In [87]:
merged_feat_collec_pd_123of3_edit_vC = merged_feat_collec_pd_123of3vB.copy(deep=True)

In [88]:
#### featureCollectionInput = merged_feat_collec_pd_123of3_edit_vC
#### jobSciIndustryInput = job_names

In [89]:
test_featColl_addProp = addSciAndIndToFeature(merged_feat_collec_pd_123of3_edit_vC,job_names)

number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Industry'] health
number =  1
7 each2['likely_Industry'] health
number =  2
7 each2['likely_Industry'] health
number =  0
7 each2['likely_Indust

In [129]:
test_featColl_addProp['features'][165]['properties']

{'address': '9847 Lawndale St, Houston, TX 77017, United States',
 'commpany_searched_for': 'Kinder+Morgan+Houston+Texas',
 'id': '3ef3da822c4de143511ea1b6dff9e110c03cffda',
 'job_title': 'Cell+Line',
 'name': 'Kinder Morgan Inc',
 'photos': [],
 'place_id': 'ChIJbZrhLhW9QIYRL6xFuDNzRSs',
 'rating': 3.7,
 'reference': 'CmRRAAAAERxcxmriEVOgxzLvFl4GbDTzz7bk0jsgfFwCgdXf5fd1ulAS8B-6frw4Ns3--5di5lll5eq_UEqp6ByStZj4Ll3a8XEyQYH7lYMrCoV82wBaJFrH2DZDANhT-E0uqnzvEhA3hn3Yh6Ps02hCjAr2jB4aGhQ3pmk1Z72G4BOfS5xHJr5VHYcuOw',
 'types': ['point_of_interest', 'establishment']}

In [68]:
test_featColl_addProp['features'][0]



{'geometry': {'coordinates': [-95.3996299, 29.70984659999999],
  'type': 'Point'},
 'properties': {'address': '6565 Fannin St, Houston, TX 77030, United States',
  'commpany_searched_for': 'Houston+Methodist+Houston+Texas',
  'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55',
  'job_title': 'Biochemistry',
  'name': 'Methodist Hospital Emergency Services',
  'nonsense': 'no really nonsense',
  'photos': [],
  'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA',
  'rating': 3.4,
  'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv',
  'types': ['hospital', 'point_of_interest', 'establishment']},
 'type': 'Feature'}

In [127]:
merged_feat_collec_pd_123of3_edit_vC.head(2)["features"][0]

{'geometry': {'coordinates': [-95.3996299, 29.70984659999999],
  'type': 'Point'},
 'properties': {'address': '6565 Fannin St, Houston, TX 77030, United States',
  'commpany_searched_for': 'Houston+Methodist+Houston+Texas',
  'id': 'aa6773412906ccba5c9a7fc7311bf947487ccd55',
  'job_title': 'Biochemistry',
  'name': 'Methodist Hospital Emergency Services',
  'nonsense': 'no really nonsense',
  'photos': [],
  'place_id': 'ChIJ67LmOXHAQIYRVm8eii2x5gA',
  'rating': 3.4,
  'reference': 'ClRQAAAAMKbMZOEOcqiCfvQn-3XzYO7oIngR90UZ2m4HmiLaeytAcUYKyvlL7KxlTPmJHc7FLDyWHTZ1yurBTmeBAuheySOArAcGsSBIpZVYtAS57u4SEPFJFMZVbPWLJwi_NjLcNMQaFHcIMFzgaJKSdvSzG555jnS-kkBv',
  'types': ['hospital', 'point_of_interest', 'establishment']},
 'type': 'Feature'}

In [98]:
job_names.head(2)

Job_Title likely_Industry field_of_science
0  Bioanalytical Scientist          health          biology
1               Biochemist          health          biology

In [114]:
job_names_dict = {}
for n in range(len(job_names)):
    row = job_names.ix[n,:]
    job_names_dict[row[0]] = [row[1], row[2]]

In [117]:
new_df  = pd.to_df([merged_feat_collec_pd_123of3_edit_vC.columns])

AttributeError: module 'pandas' has no attribute 'to_df'

In [ ]:
def add_industry(merged_features, job_dict):
    # initialize new df here
    output_df
    for i in range(len(merged_features)):
        row = merged_features.ix[i,:]
        feat_dict = row[0]
        feat_dict['properties']['features']['job_type'] = job_dict[feat_dict['properties']['features']['job_title']]
        output_df.append([feat_dict, row[1]])
        
    return output_df
        
        